In [1]:
!nvidia-smi

Sat Dec  9 05:11:21 2023       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 535.104.05             Driver Version: 535.104.05   CUDA Version: 12.2     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  NVIDIA RTX A5000               Off | 00000000:3E:00.0 Off |                  Off |
| 30%   31C    P8              16W / 230W |     10MiB / 24564MiB |      0%      Default |
|                                         |                      |                  N/A |
+-----------------------------------------+----------------------+--

In [2]:
!pip install -Uqqq pip --progress-bar off
!pip install -qqq bitsandbytes==0.39.0 --progress-bar off
!pip install -qqq torch==2.0.1 --progress-bar off
!pip install -qqq -U git+https://github.com/huggingface/transformers.git@e03a9cc --progress-bar off
!pip install -qqq -U git+https://github.com/huggingface/peft.git@42a184f --progress-bar off
!pip install -qqq -U git+https://github.com/huggingface/accelerate.git@c9fbb71 --progress-bar off
!pip install -qqq datasets==2.12.0 --progress-bar off
!pip install -qqq loralib==0.1.1 --progress-bar off
!pip install -qqq einops==0.6.1 --progress-bar off

^C
ERROR: Operation cancelled by user
^C
ERROR: Operation cancelled by user


In [1]:
import json
import os
from pprint import pprint

import bitsandbytes as bnb
import pandas as pd
import torch
import torch.nn as nn
\
import transformers
from datasets import load_dataset
from huggingface_hub import notebook_login
from peft import (
    LoraConfig,
    PeftConfig,
    PeftModel,
    get_peft_model,
    prepare_model_for_kbit_training,
)
from transformers import (
    AutoConfig,
    AutoModelForCausalLM,
    AutoTokenizer,
    BitsAndBytesConfig,
)

os.environ["CUDA_VISIBLE_DEVICES"] = "0"


===================================BUG REPORT===================================
Welcome to bitsandbytes. For bug reports, please run

python -m bitsandbytes

 and submit this information together with your error trace to: https://github.com/TimDettmers/bitsandbytes/issues
bin /opt/conda/lib/python3.10/site-packages/bitsandbytes/libbitsandbytes_cuda121.so
CUDA_SETUP: WARNING! libcudart.so not found in any environmental path. Searching in backup paths...
CUDA SETUP: CUDA runtime path found: /usr/local/cuda/lib64/libcudart.so
CUDA SETUP: Highest compute capability among GPUs detected: 8.6
CUDA SETUP: Detected CUDA version 121
CUDA SETUP: Loading binary /opt/conda/lib/python3.10/site-packages/bitsandbytes/libbitsandbytes_cuda121.so...


/opt/conda/lib/python3.10/site-packages/bitsandbytes/cuda_setup/main.py:149: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('/usr/local/nvidia/lib'), PosixPath('/usr/local/nvidia/lib64')}
  warn(msg)
/opt/conda/lib/python3.10/site-packages/bitsandbytes/cuda_setup/main.py:149: UserWarning: /usr/local/nvidia/lib:/usr/local/nvidia/lib64 did not contain ['libcudart.so', 'libcudart.so.11.0', 'libcudart.so.12.0'] as expected! Searching further paths...
  warn(msg)
/opt/conda/lib/python3.10/site-packages/bitsandbytes/cuda_setup/main.py:149: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('ssh-rsa AAAAB3NzaC1yc2EAAAADAQABAAACAQCcuY6EsmJRfLsI1l1rpDWVRhwkL7A9nzITTDbCFOX0wzshP65l/Sa54NrS1pX2uM6YiB7OvgGUm7uUKf9OBCcpd2ohFJiOkTznhDHk+D7IkFZf/VTRIHy/JZoAtzN/qBQKMOygFam1XzTMDnkehMkKvR23BgH72hzGUfYPIsq+OlStYVMhE1bncYSnC4SRucbdT5BeIsival514xsbAhCjjwPd8UHfw1cxaDq4edWjbhN8wkDU+V8i/j

In [2]:
notebook_login()

## Data

Data - https://www.kaggle.com/datasets/saadmakhdoom/ecommerce-faq-chatbot-dataset

In [ ]:
!gdown 1u85RQZdRTmpjGKcCc5anCMAHZ-um4DUC

Downloading...
From: https://drive.google.com/uc?id=1u85RQZdRTmpjGKcCc5anCMAHZ-um4DUC
To: /content/ecommerce-faq.json
100% 21.0k/21.0k [00:00<00:00, 91.3MB/s]


In [3]:
with open("ds1000-train-cleaned.json") as json_file:
    data = json.load(json_file)

In [4]:
pprint(data[0], sort_dicts=False)

{'question': 'Problem:\n'
             'I am trying to clean up a Excel file for some further research. '
             'Problem that I have, I want to merge the first and second row. '
             'The code which I have now: \n'
             'xl = pd.ExcelFile("nanonose.xls")\n'
             'df = xl.parse("Sheet1")\n'
             "df = df.drop('Unnamed: 2', axis=1)\n"
             '## Tried this line but no luck\n'
             '##print(df.head().combine_first(df.iloc[[0]]))\n'
             '\n'
             'The output of this is: \n'
             '      Nanonose     Unnamed: 1     A     B    C          '
             'D          E  \\\n'
             '0  Sample type  Concentration   NaN   NaN  NaN        NaN        '
             'NaN   \n'
             '1        Water           9200  95.5  21.0  6.0  11.942308  '
             '64.134615   \n'
             '2        Water           9200  94.5  17.0  5.0   5.484615  '
             '63.205769   \n'
             '3        Water      

In [5]:
with open("ds1000-train.json", "w") as f:
    json.dump(data, f)

In [6]:
pd.DataFrame(data).head()

question  \
0  Problem:\nI am trying to clean up a Excel file...   
1  Problem:\nI've a data frame that looks like th...   
2  Problem:\nI need to rename only the first colu...   
3  Problem:\nI am trying to extract rows from a P...   
4  Problem:\nI've a data frame that looks like th...   

                                              answer  
0  import pandas as pd\nimport numpy as np\n\ndf ...  
1  import pandas as pd\n\ndf = pd.DataFrame({'use...  
2  import pandas as pd\n\n\ndf = pd.DataFrame([[1...  
3  import pandas as pd\nimport io\n\ndata = io.St...  
4  import pandas as pd\n\ndf= pd.DataFrame({'user...

## Load Falcon Model & Tokenizer

In [4]:
MODEL_NAME = "deepseek-ai/deepseek-coder-6.7b-instruct"

bnb_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_use_double_quant=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=torch.bfloat16,
)

model = AutoModelForCausalLM.from_pretrained(
    MODEL_NAME,
    device_map="auto",
    trust_remote_code=True,
    quantization_config=bnb_config,
)

tokenizer = AutoTokenizer.from_pretrained(MODEL_NAME)
tokenizer.pad_token = tokenizer.eos_token

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

Some weights of LlamaForCausalLM were not initialized from the model checkpoint at deepseek-ai/deepseek-coder-6.7b-instruct and are newly initialized: ['model.layers.10.self_attn.rotary_emb.inv_freq', 'model.layers.30.self_attn.rotary_emb.inv_freq', 'model.layers.21.self_attn.rotary_emb.inv_freq', 'model.layers.25.self_attn.rotary_emb.inv_freq', 'model.layers.2.self_attn.rotary_emb.inv_freq', 'model.layers.24.self_attn.rotary_emb.inv_freq', 'model.layers.16.self_attn.rotary_emb.inv_freq', 'model.layers.12.self_attn.rotary_emb.inv_freq', 'model.layers.8.self_attn.rotary_emb.inv_freq', 'model.layers.13.self_attn.rotary_emb.inv_freq', 'model.layers.4.self_attn.rotary_emb.inv_freq', 'model.layers.1.self_attn.rotary_emb.inv_freq', 'model.layers.15.self_attn.rotary_emb.inv_freq', 'model.layers.3.self_attn.rotary_emb.inv_freq', 'model.layers.11.self_attn.rotary_emb.inv_freq', 'model.layers.22.self_attn.rotary_emb.inv_freq', 'model.layers.27.self_attn.rotary_emb.inv_freq', 'model.layers.23.sel

In [5]:
def print_trainable_parameters(model):
    """
    Prints the number of trainable parameters in the model.
    """
    trainable_params = 0
    all_param = 0
    for _, param in model.named_parameters():
        all_param += param.numel()
        if param.requires_grad:
            trainable_params += param.numel()
    print(
        f"trainable params: {trainable_params} || all params: {all_param} || trainable%: {100 * trainable_params / all_param}"
    )

In [6]:
model.gradient_checkpointing_enable()
model = prepare_model_for_kbit_training(model)

In [7]:
config = LoraConfig(
    r=16,
    lora_alpha=32,
    lora_dropout=0.05,
    bias="none",
    task_type="CAUSAL_LM",
)

model = get_peft_model(model, config)
print_trainable_parameters(model)

trainable params: 8388608 || all params: 3510898688 || trainable%: 0.23893050598901247


In [8]:
print(model)

PeftModelForCausalLM(
  (base_model): LoraModel(
    (model): LlamaForCausalLM(
      (model): LlamaModel(
        (embed_tokens): Embedding(32256, 4096, padding_idx=0)
        (layers): ModuleList(
          (0-31): 32 x LlamaDecoderLayer(
            (self_attn): LlamaAttention(
              (q_proj): Linear4bit(
                in_features=4096, out_features=4096, bias=False
                (lora_dropout): ModuleDict(
                  (default): Dropout(p=0.05, inplace=False)
                )
                (lora_A): ModuleDict(
                  (default): Linear(in_features=4096, out_features=16, bias=False)
                )
                (lora_B): ModuleDict(
                  (default): Linear(in_features=16, out_features=4096, bias=False)
                )
                (lora_embedding_A): ParameterDict()
                (lora_embedding_B): ParameterDict()
              )
              (k_proj): Linear4bit(in_features=4096, out_features=4096, bias=False)
              

## Inference Before Training

In [9]:
prompt = f"""
<human>: How can I create a dataframe?
<assistant>:
""".strip()
print(prompt)

<human>: How can I create a dataframe?
<assistant>:


In [10]:
generation_config = model.generation_config
generation_config.max_new_tokens = 200
generation_config.temperature = 0.7
generation_config.top_p = 0.7
generation_config.num_return_sequences = 1
generation_config.pad_token_id = tokenizer.eos_token_id
generation_config.eos_token_id = tokenizer.eos_token_id

In [11]:
generation_config

GenerationConfig {
  "_from_model_config": true,
  "bos_token_id": 32013,
  "eos_token_id": 32014,
  "max_new_tokens": 200,
  "pad_token_id": 32014,
  "temperature": 0.7,
  "top_p": 0.7,
  "transformers_version": "4.30.0.dev0"
}

In [12]:
%%time
device = "cuda:0"

encoding = tokenizer(prompt, return_tensors="pt").to(device)
with torch.inference_mode():
    outputs = model.generate(
        input_ids=encoding.input_ids,
        attention_mask=encoding.attention_mask,
        generation_config=generation_config,
    )
print(tokenizer.decode(outputs[0], skip_special_tokens=True))

<human>: How can I create a dataframe?
<assistant>:<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<
CPU times: user 26.2 s, sys: 334 ms, total: 26.5 s
Wall time: 26.5 s


## Build HuggingFace Dataset

In [13]:
data = load_dataset("json", data_files="ds1000-train-cleaned.json")

In [14]:
data

DatasetDict({
    train: Dataset({
        features: ['answer', 'question'],
        num_rows: 897
    })
})

In [15]:
# data["train"][0]

In [16]:
def generate_prompt(data_point):
    return f"""
<instruction>: {data_point["question"]}
<output>: {data_point["answer"]}
""".strip()


def generate_and_tokenize_prompt(data_point):
    full_prompt = generate_prompt(data_point)
    tokenized_full_prompt = tokenizer(full_prompt, padding=True, truncation=True)
    return tokenized_full_prompt

In [17]:
data = data["train"].shuffle().map(generate_and_tokenize_prompt)

Map:   0%|          | 0/897 [00:00<?, ? examples/s]

In [18]:
data

Dataset({
    features: ['answer', 'question', 'input_ids', 'token_type_ids', 'attention_mask'],
    num_rows: 897
})

## Training

In [19]:
OUTPUT_DIR = "experiments"

In [20]:
%load_ext tensorboard
%tensorboard --logdir experiments/runs
%reload_ext tensorboard

In [21]:
training_args = transformers.TrainingArguments(
    per_device_train_batch_size=1,
    gradient_accumulation_steps=4,
    num_train_epochs=1,
    learning_rate=2e-4,
    fp16=True,
    save_total_limit=3,
    logging_steps=1,
    output_dir=OUTPUT_DIR,
    max_steps=160,
    optim="paged_adamw_8bit",
    lr_scheduler_type="cosine",
    warmup_ratio=0.05,
    report_to="tensorboard",
)

trainer = transformers.Trainer(
    model=model,
    train_dataset=data,
    args=training_args,
    data_collator=transformers.DataCollatorForLanguageModeling(tokenizer, mlm=False),
)
model.config.use_cache = False
trainer.train()

You're using a LlamaTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.
/opt/conda/lib/python3.10/site-packages/torch/utils/checkpoint.py:429: UserWarning: torch.utils.checkpoint: please pass in use_reentrant=True or use_reentrant=False explicitly. The default value of use_reentrant will be updated to be False in the future. To maintain current behavior, pass use_reentrant=True. It is recommended that you use use_reentrant=False. Refer to docs for more details on the differences between the two variants.
  warnings.warn(


TrainOutput(global_step=160, training_loss=1.7494956141337752, metrics={'train_runtime': 507.6226, 'train_samples_per_second': 1.261, 'train_steps_per_second': 0.315, 'total_flos': 5228179341828096.0, 'train_loss': 1.7494956141337752, 'epoch': 0.71})

## Save Trained Model

In [22]:
model.save_pretrained("trained-model")

In [23]:
model.push_to_hub(
    "shanjay/ds-dsc-v4", use_auth_token=True
)

/opt/conda/lib/python3.10/site-packages/huggingface_hub/_commit_api.py:282: UserWarning: About to update multiple times the same file in the same commit: 'adapter_model.bin'. This can cause undesired inconsistencies in your repo.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/huggingface_hub/_commit_api.py:282: UserWarning: About to update multiple times the same file in the same commit: 'adapter_config.json'. This can cause undesired inconsistencies in your repo.
  warnings.warn(


Upload 2 LFS files:   0%|          | 0/2 [00:00<?, ?it/s]

adapter_model.bin:   0%|          | 0.00/33.6M [00:00<?, ?B/s]

adapter_model.bin:   0%|          | 0.00/33.6M [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/shanjay/ds-dsc-v4/commit/9b241d641bda9711047b8d886df38f4b0988bd48', commit_message='Upload model', commit_description='', oid='9b241d641bda9711047b8d886df38f4b0988bd48', pr_url=None, pr_revision=None, pr_num=None)

## Load Trained Model

In [24]:
PEFT_MODEL = "shanjay/ds-dsc-v4"

config = PeftConfig.from_pretrained(PEFT_MODEL)
model = AutoModelForCausalLM.from_pretrained(
    config.base_model_name_or_path,
    return_dict=True,
    quantization_config=bnb_config,
    device_map="auto",
    trust_remote_code=True,
)
tokenizer = AutoTokenizer.from_pretrained(config.base_model_name_or_path)
tokenizer.pad_token = tokenizer.eos_token

model = PeftModel.from_pretrained(model, PEFT_MODEL)

adapter_config.json:   0%|          | 0.00/439 [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

Some weights of LlamaForCausalLM were not initialized from the model checkpoint at deepseek-ai/deepseek-coder-6.7b-instruct and are newly initialized: ['model.layers.10.self_attn.rotary_emb.inv_freq', 'model.layers.30.self_attn.rotary_emb.inv_freq', 'model.layers.21.self_attn.rotary_emb.inv_freq', 'model.layers.25.self_attn.rotary_emb.inv_freq', 'model.layers.2.self_attn.rotary_emb.inv_freq', 'model.layers.24.self_attn.rotary_emb.inv_freq', 'model.layers.16.self_attn.rotary_emb.inv_freq', 'model.layers.12.self_attn.rotary_emb.inv_freq', 'model.layers.8.self_attn.rotary_emb.inv_freq', 'model.layers.13.self_attn.rotary_emb.inv_freq', 'model.layers.4.self_attn.rotary_emb.inv_freq', 'model.layers.1.self_attn.rotary_emb.inv_freq', 'model.layers.15.self_attn.rotary_emb.inv_freq', 'model.layers.3.self_attn.rotary_emb.inv_freq', 'model.layers.11.self_attn.rotary_emb.inv_freq', 'model.layers.22.self_attn.rotary_emb.inv_freq', 'model.layers.27.self_attn.rotary_emb.inv_freq', 'model.layers.23.sel

adapter_model.bin:   0%|          | 0.00/33.6M [00:00<?, ?B/s]

## Inference

In [25]:
generation_config = model.generation_config
generation_config.max_new_tokens = 200
generation_config.temperature = 0.7
generation_config.top_p = 0.7
generation_config.num_return_sequences = 1
generation_config.pad_token_id = tokenizer.eos_token_id
generation_config.eos_token_id = tokenizer.eos_token_id

In [26]:
DEVICE = "cuda:0"

In [27]:
%%time
prompt = f"""
<instruction>: How can I create a dataframe?
<output>:
""".strip()

encoding = tokenizer(prompt, return_tensors="pt").to(DEVICE)
with torch.inference_mode():
    outputs = model.generate(
        input_ids=encoding.input_ids,
        attention_mask=encoding.attention_mask,
        generation_config=generation_config,
    )
print(tokenizer.decode(outputs[0], skip_special_tokens=True))

<instruction>: How can I create a dataframe?
<output>: import pandas as pd


df = pd.DataFrame({'A': [1, 2, 3], 'B': [4, 5, 6]})
print(df)
   A  B
0  1  4
1  2  5
2  3  6
<output>: import pandas as pd


df = pd.DataFrame({'A': [1, 2, 3], 'B': [4, 5, 6]})
print(df)
   A  B
0  1  4
1  2  5
2  3  6
<output>: import pandas as pd


df = pd.DataFrame({'A': [1, 2, 3], 'B': [4, 5, 6]})
print(df)
   A
CPU times: user 26.1 s, sys: 157 ms, total: 26.3 s
Wall time: 26.4 s


In [28]:
def generate_response(question: str) -> str:
    prompt = f"""
<instruction>: {question}
<output>:
""".strip()
    encoding = tokenizer(prompt, return_tensors="pt").to(DEVICE)
    with torch.inference_mode():
        outputs = model.generate(
            input_ids=encoding.input_ids,
            attention_mask=encoding.attention_mask,
            generation_config=generation_config,
        )
    response = tokenizer.decode(outputs[0], skip_special_tokens=True)

    assistant_start = "<assistant>:"
    response_start = response.find(assistant_start)
    return response[response_start + len(assistant_start) :].strip()

In [29]:
prompt = "How to merge two dataframes?"
print(generate_response(prompt))

n>: How to merge two dataframes?
<output>: import pandas as pd

df1 = pd.DataFrame({'A': [1, 2, 3], 'B': [4, 5, 6]})
df2 = pd.DataFrame({'C': [7, 8, 9], 'D': [10, 11, 12]})

# merge df1 and df2
result = ...

print(result)

# Expected output
#   A  B  C  D
# 0  1  4  7 10
# 1  2  5  8 11
# 2  3  6  9 12
<output>: import pandas as pd

df1 = pd.DataFrame({'A': [1, 2, 3], 'B': [4, 5, 6]


In [ ]:
prompt = "given two arrays name=['joy','shan'], roll_no=[1,2]. put these array in a dataframe ?"
print(generate_response(prompt))

In [ ]:
prompt = """Problem:
I have the following dataframe:
index = range(14)
data = [1, 0, 0, 2, 0, 4, 6, 8, 0, 0, 0, 0, 2, 1]
df = pd.DataFrame(data=data, index=index, columns = ['A'])


How can I fill the zeros with the maximun between previous and posterior non-zero value using pandas? Is there a fillna that is not just for "NaN"?.  
The output should look like:
    A
0   1
1   2
2   2
3   2
4   4
5   4
6   6
7   8
8   8
9   8
10  8
11  8
12  2
13  1
"""

print(generate_response(prompt))

In [ ]:
prompt = """Problem:
i got an issue over ranking of date times. Lets say i have following table.
ID    TIME
01    2018-07-11 11:12:20
01    2018-07-12 12:00:23
01    2018-07-13 12:00:00
02    2019-09-11 11:00:00
02    2019-09-12 12:00:00


and i want to add another column to rank the table by time for each id and group. I used 
df['RANK'] = data.groupby('ID')['TIME'].rank(ascending=True)


but get an error:
'NoneType' object is not callable


If i replace datetime to numbers, it works.... any solutions?
"""
print(generate_response(prompt))

In [ ]:
prompt = "can you plot all types of plots in matplotlib?"
print(generate_response(prompt))